In [0]:
import pyspark.sql.functions as F
import os

STORAGE_ACCOUNT = os.getenv('STORAGE_ACCOUNT')
STORAGE_ACCOUNT_KEY = os.getenv('STORAGE_ACCOUNT_KEY')
spark.conf.set(STORAGE_ACCOUNT, STORAGE_ACCOUNT_KEY)


In [0]:
colombian_df = spark.read\
                 .option("header", "true")\
                 .option("inferSchema", "true")\
                 .csv("abfss://datasets@tfmstorageacc.dfs.core.windows.net/violencia_intrafamiliar_colombia.csv")

colombian_df.display()

ID Año del hecho Sexo de la victima Grupo de edad de la victima Grupo Mayor Menor de Edad Edad judicial Ciclo Vital País de Nacimiento de la Víctima Escolaridad Estado Civil Tipo de Discapacidad Pertenencia Étnica Pertenencia Grupal Mes del hecho Dia del hecho Rango de Hora del Hecho X 3 Horas Código Dane Municipio Municipio del hecho DANE Departamento del hecho DANE Código Dane Departamento Localidad del Hecho Zona del Hecho Escenario del Hecho Actividad Durante el Hecho Circunstancia del Hecho Contexto de violencia Mecanismo Causal Diagnostico Topográfico de la Lesión Sexo del Presunto Agresor Presunto Agresor Condición de la Víctima Medio de Desplazamiento o Transporte Servicio del Vehículo Clase o Tipo de Accidente Objeto de Colisión Servicio del Objeto de Colisión Días de Incapacidad Medicolegal 1 2015 Hombre (10 a 14) a) Menores de Edad (<18 años) (10 a 13) (12 a 17) Adolescencia Colombia Educación básica primaria Soltero (a) Ninguna Sin información Sin información Diciembre Martes 18:00 a 20:59 11001 Bogotá, D.C. Bogotá, D.C. 11 Rafael Uribe Uribe Cabecera municipal Calle (autopista, avenida, dentro de la ciudad) Actividades de desplazamiento de un lugar a otro Violencia a niños, niñas y adolescentes Violencia Contra Niños, Niñas y Adolescentes (VIF) Abrasivo Trauma de miembros Hombre Padre No aplica No aplica No aplica No aplica No aplica No aplica 1 a 30 2 2015 Hombre (00 a 04) a) Menores de Edad (<18 años) (00 a 04) (00 a 05) Primera Infancia Colombia Sin escolaridad No aplica Ninguna Sin pertenencia étnica Sin información Marzo Miércoles 18:00 a 20:59 25754 Soacha Cundinamarca 25 No aplica Cabecera municipal Vivienda Actividades relacionadas con la asistencia a eventos culturales, de entretenimiento y/o deportivos Violencia a niños, niñas y adolescentes Violencia Contra Niños, Niñas y Adolescentes (VIF) Contundente Trauma de miembros Mujer Madre No aplica No aplica No aplica No aplica No aplica No aplica 1 a 30 3 2015 Hombre (00 a 04) a) Menores de Edad (<18 años) (00 a 04) (00 a 05) Primera Infancia Colombia Sin escolaridad No aplica Ninguna Sin pertenencia étnica Sin información Junio Jueves Sin información 25754 Soacha Cundinamarca 25 No aplica Cabecera municipal Sin Información Actividades de desplazamiento de un lugar a otro Violencia a niños, niñas y adolescentes Violencia Contra Niños, Niñas y Adolescentes (VIF) Por determinar Sin información Mujer Otros familiares civiles o consanguíneos No aplica No aplica No aplica No aplica No aplica No aplica Sin información 4 2015 Hombre (00 a 04) a) Menores de Edad (<18 años) (00 a 04) (00 a 05) Primera Infancia Colombia Sin escolaridad No aplica Ninguna Sin pertenencia étnica Sin información Enero Sábado 06:00 a 08:59 54001 Cúcuta Norte de Santander 54 No aplica Cabecera municipal Vivienda Actividades de desplazamiento de un lugar a otro Violencia a niños, niñas y adolescentes Violencia Contra Niños, Niñas y Adolescentes (VIF) Contundente Trauma facial Mujer Abuelo (a) No aplica No aplica No aplica No aplica No aplica No aplica 1 a 30 5 2015 Hombre (25 a 29) b) Mayores de Edad (>18 años) (25 a 28) (18 a 28) Juventud Colombia Sin información Unión libre Ninguna Sin información Sin información Mayo Martes 09:00 a 11:59 11001 Bogotá, D.C. Bogotá, D.C. 11 Usme Cabecera municipal Calle (autopista, avenida, dentro de la ciudad) Actividades de desplazamiento de un lugar a otro Violencia entre otros familiares Violencia Entre Otros Familiares (VIF) Contundente Trauma facial Hombre Hermano (a) No aplica No aplica No aplica No aplica No aplica No aplica 1 a 30 6 2015 Mujer (00 a 04) a) Menores de Edad (<18 años) (00 a 04) (00 a 05) Primera Infancia Colombia Sin escolaridad No aplica Ninguna Sin pertenencia étnica Sin información Marzo Viernes 09:00 a 11:59 50001 Villavicencio Meta 50 No aplica Cabecera municipal Vivienda Actividades vitales o relacionadas con el cuidado personal Violencia a niños, niñas y adolescentes Violencia Contra Niños, Niñas y Adolescentes (VIF) Contunden

Data is pretty clean already the task here is to aggregate the data into statistics, we only need to filter for Female victims and group perpetrators into partner/not_partner/any 

In [0]:
colombian_df.select(
    'Presunto Agresor',
).distinct().display()

Presunto Agresor Padre Nieto (a) Ex Esposo (a) Hermanastro (a) Ex compañero (a) permanente Suegro (a) Abuelo (a) Ex esposo (a) YERNO Ex Compañero (a) sentimental Tío (a) NUERA Compañero (a) permanente Profesor (a) Cuñado (a) Novio (a) Madre Nuera Ex Novio (a) Sin información Otros familiares civiles o consanguíneos Hijo (a) Padrastro Hijastro (a) Sobrino (a) Hermano (a) Amante Yerno Ex Amante Madrastra Primo (a) Encargado del cuidado Esposo (a) Ex novio (a) Ex amante Pareja o Expareja

In [0]:
colombian_df_filtered = colombian_df.where(
    F.col('Sexo de la victima') == 'Mujer'
).withColumn(
    'age_group',
    F.when(F.col('Grupo Mayor Menor de Edad') == 'b) Mayores de Edad (>18 años)', 'adult').otherwise('child')
).withColumn(
    'country',
    F.lit('Colombia'),
).withColumn(
    'perpetrator',
    F.when(F.col('Presunto Agresor').isin(
        'Amante',
        'Compañero (a) permanente',
        'Esposo (a)',
        'Pareja o Expreja',
        'Novio (a)',
    ), 'partner').otherwise('non-partner')
).select(
    F.col('country'),
    F.col('Departamento del hecho DANE').alias('department'),
    F.col('Año del hecho').alias('year'),
    F.col('perpetrator'),
    F.col('age_group'),
).cache()
colombian_df_filtered.display()

country department year perpetrator age_group Colombia Meta 2015 non-partner child Colombia Huila 2015 non-partner child Colombia Sucre 2015 partner adult Colombia Bogotá, D.C. 2015 non-partner adult Colombia Antioquia 2015 non-partner adult Colombia Valle del Cauca 2015 non-partner adult Colombia Cesar 2015 non-partner child Colombia Atlántico 2015 non-partner child Colombia Bogotá, D.C. 2015 non-partner child Colombia La Guajira 2015 non-partner child Colombia Valle del Cauca 2015 non-partner adult Colombia Caldas 2015 non-partner adult Colombia Casanare 2015 non-partner child Colombia Bolívar 2015 non-partner child Colombia Valle del Cauca 2015 non-partner adult Colombia Bogotá, D.C. 2015 non-partner adult Colombia Quindío 2015 non-partner adult Colombia Bogotá, D.C. 2015 non-partner adult Colombia Meta 2015 non-partner adult Colombia Santander 2015 non-partner adult Colombia Nariño 2015 non-partner adult Colombia Meta 2015 non-partner child Colombia Antioquia 2015 non-partner adult Colombia Antioquia 2015 non-partner adult Colombia Bogotá, D.C. 2015 non-partner adult Colombia Antioquia 2015 non-partner adult Colombia Cundinamarca 2015 non-partner adult Colombia Bogotá, D.C. 2015 non-partner adult Colombia Caldas 2015 non-partner adult Colombia Caldas 2015 non-partner adult Colombia Santander 2015 non-partner adult Colombia Atlántico 2015 non-partner adult Colombia Bogotá, D.C. 2015 non-partner adult Colombia Bolívar 2015 non-partner adult Colombia Bogotá, D.C. 2015 non-partner adult Colombia Córdoba 2015 non-partner adult Colombia Norte de Santander 2015 non-partner adult Colombia Norte de Santander 2015 non-partner child Colombia Archipiélago de San Andrés, Providencia y Santa Catalina 2015 non-partner child Colombia Quindío 2015 non-partner adult Colombia Bogotá, D.C. 2015 non-partner adult Colombia Antioquia 2015 non-partner adult Colombia Antioquia 2015 non-partner adult Colombia Atlántico 2015 non-partner adult Colombia Atlántico 2015 non-partner adult Colombia Antioquia 2015 non-partner child Colombia Tolima 2015 non-partner child Colombia Meta 2015 non-partner adult Colombia Cauca 2015 non-partner adult Colombia Bogotá, D.C. 2015 non-partner adult Colombia Bogotá, D.C. 2015 non-partner adult Colombia Cundinamarca 2015 non-partner adult Colombia Valle del Cauca 2015 non-partner adult Colombia Tolima 2015 non-partner adult Colombia Antioquia 2015 non-partner adult Colombia Archipiélago de San Andrés, Providencia y Santa Catalina 2015 non-partner adult Colombia Antioquia 2015 non-partner adult Colombia Cundinamarca 2015 non-partner adult Colombia Boyacá 2015 non-partner child Colombia Caldas 2015 non-partner adult Colombia Huila 2015 non-partner adult Colombia Huila 2015 non-partner adult Colombia Bogotá, D.C. 2015 non-partner adult Colombia Norte de Santander 2015 non-partner child Colombia Magdalena 2015 non-partner child Colombia Santander 2015 non-partner adult Colombia Bolívar 2015 non-partner child Colombia Bolívar 2015 non-partner child Colombia Valle del Cauca 2015 non-partner adult Colombia Cesar 2015 non-partner adult Colombia Santander 2015 non-partner child Colombia Santander 2015 non-partner adult Colombia Nariño 2015 non-partner adult Colombia Bogotá, D.C. 2015 non-partner adult Colombia Cundinamarca 2015 non-partner adult Colombia Bogotá, D.C. 2015 non-partner adult Colombia Santander 2015 non-partner adult Colombia Huila 2015 non-partner adult Colombia Meta 2015 non-partner child Colombia Antioquia 2015 non-partner adult Colombia Nariño 2015 non-partner adult Colombia Antioquia 2015 non-partner adult Colombia Bogotá, D.C. 2015 non-partner child Colombia Tolima 2015 non-partner adult Colombia Nariño 2015 non-partner adult Colombia Atlántico 2015 non-partner child Colombia Nariño 2015 non-partner adult Colombia Cundinamarca 2015 non-partner adult Colombia Bogotá, D.C. 2015 non-partner adult Colombia Bogotá, D.C. 2015 non-partner child Colombia Bogotá, D.C. 2015 non-partner adult Colombia Risaralda 2015 no

now we need to aggregate the data grouping by all fields, and concat it to the any perpetrator

In [0]:
colombian_df_perpetrator = colombian_df_filtered.groupBy('year', 'country', 'department', 'perpetrator', 'age_group').agg(
    F.count('*').alias('total_cases')
)
colombian_df_perpetrator.display()
# for the union we need to make the columns match
colombian_df_any = colombian_df_filtered.groupBy('year', 'country', 'department', 'age_group').agg(
    F.count('*').alias('total_cases')
).withColumn(
    'perpetrator', F.lit('any')
).select(
    F.col('year'),
    F.col('country'),
    F.col('department'),
    F.col('perpetrator'),
    F.col('age_group'),
    F.col('total_cases')
)
colombian_df_any.display()

year country department perpetrator age_group total_cases 2015 Colombia Córdoba non-partner adult 314 2015 Colombia Magdalena non-partner child 111 2016 Colombia Huila non-partner adult 755 2016 Colombia Arauca partner adult 283 2015 Colombia Santander non-partner child 257 2017 Colombia Antioquia non-partner child 708 2017 Colombia Antioquia partner child 103 2015 Colombia Chocó partner adult 138 2017 Colombia Valle del Cauca partner child 55 2017 Colombia La Guajira non-partner adult 288 2016 Colombia Vichada non-partner child 3 2016 Colombia Chocó non-partner adult 122 2017 Colombia La Guajira non-partner child 47 2016 Colombia Magdalena partner adult 602 2016 Colombia Archipiélago de San Andrés, Providencia y Santa Catalina non-partner child 6 2015 Colombia Risaralda non-partner child 110 2015 Colombia Bolívar partner adult 928 2016 Colombia Valle del Cauca partner child 51 2016 Colombia Arauca partner child 12 2016 Colombia Cesar partner child 14 2017 Colombia Santander non-partner child 268 2015 Colombia La Guajira non-partner child 63 2015 Colombia Meta partner adult 773 2016 Colombia Cauca non-partner adult 666 2017 Colombia Atlántico partner adult 1243 2016 Colombia Putumayo non-partner child 42 2015 Colombia Magdalena partner adult 638 2017 Colombia Caquetá non-partner child 33 2015 Colombia Archipiélago de San Andrés, Providencia y Santa Catalina non-partner child 22 2017 Colombia Nariño partner child 21 2015 Colombia Meta non-partner adult 699 2017 Colombia Huila non-partner adult 762 2015 Colombia Bogotá, D.C. non-partner adult 4946 2015 Colombia Cauca non-partner adult 724 2015 Colombia Risaralda non-partner adult 552 2017 Colombia Caldas partner adult 259 2017 Colombia Nariño non-partner child 86 2017 Colombia Archipiélago de San Andrés, Providencia y Santa Catalina partner adult 73 2015 Colombia Norte de Santander partner child 19 2017 Colombia Nariño non-partner adult 625 2017 Colombia Caldas non-partner child 74 2015 Colombia Putumayo partner child 9 2016 Colombia La Guajira partner adult 276 2015 Colombia Bogotá, D.C. non-partner child 1799 2017 Colombia Bolívar partner child 28 2015 Colombia Caquetá non-partner adult 116 2015 Colombia Guaviare partner adult 24 2015 Colombia Tolima partner adult 516 2016 Colombia Santander partner child 52 2016 Colombia Guaviare partner adult 21 2017 Colombia Casanare partner child 15 2015 Colombia Bolívar non-partner child 111 2016 Colombia Risaralda non-partner adult 535 2015 Colombia Bogotá, D.C. partner child 140 2017 Colombia Cundinamarca non-partner child 488 2016 Colombia Tolima non-partner child 144 2016 Colombia Guainía non-partner child 6 2016 Colombia Antioquia non-partner adult 3095 2016 Colombia Arauca non-partner adult 273 2016 Colombia Risaralda partner adult 415 2017 Colombia Putumayo partner adult 148 2017 Colombia Bogotá, D.C. partner adult 6625 2017 Colombia Sucre non-partner adult 452 2017 Colombia Casanare partner adult 527 2017 Colombia Bogotá, D.C. non-partner child 1911 2017 Colombia La Guajira partner child 10 2015 Colombia Nariño non-partner child 83 2016 Colombia Norte de Santander partner child 23 2015 Colombia Cundinamarca non-partner adult 1661 2017 Colombia Nariño partner adult 594 2015 Colombia Amazonas non-partner child 18 2015 Colombia Guaviare partner child 1 2015 Colombia Valle del Cauca partner adult 1611 2015 Colombia Cundinamarca non-partner child 587 2016 Colombia Huila partner child 31 2017 Colombia Amazonas non-partner adult 59 2015 Colombia Guainía non-partner adult 19 2015 Colombia Amazonas partner adult 61 2016 Colombia Amazonas non-partner adult 78 2015 Colombia Huila non-partner child 183 2015 Colombia Cauca partner child 14 2017 Colombia Archipiélago de San Andrés, Providencia y Santa Catalina partner child 4 2015 Colombia Cesar partner child 8 2016 Colombia Amazonas partner adult 51 2017 Colombia Amazonas partner adult 59 2016 Colombia Antioquia partner adult 2385 2016 Colombia Amazonas partner child 1 2015 Colombia Tolima par

year country department perpetrator age_group total_cases 2017 Colombia Cundinamarca any adult 3933 2022 Colombia Caldas any adult 481 2015 Colombia Casanare any adult 746 2017 Colombia Cesar any adult 1138 2016 Colombia Tolima any adult 1499 2015 Colombia Huila any child 217 2015 Colombia Tolima any child 153 2017 Colombia Quindío any child 98 2015 Colombia Nariño any child 107 2016 Colombia Boyacá any adult 1896 2017 Colombia Chocó any adult 209 2016 Colombia Norte de Santander any adult 1511 2017 Colombia Guainía any adult 27 2015 Colombia Casanare any child 152 2017 Colombia Guainía any child 6 2016 Colombia Valle del Cauca any adult 3721 2016 Colombia Cundinamarca any child 600 2015 Colombia Meta any child 259 2016 Colombia Huila any child 167 2015 Colombia Antioquia any adult 5476 2016 Colombia La Guajira any adult 554 2017 Colombia Huila any adult 1599 2017 Colombia Meta any adult 1873 2017 Colombia Putumayo any adult 268 2017 Colombia Atlántico any child 233 2017 Colombia Guaviare any adult 46 2015 Colombia Caquetá any child 16 2017 Colombia Valle del Cauca any child 345 2015 Colombia Norte de Santander any adult 1675 2017 Colombia Sucre any adult 753 2015 Colombia Chocó any child 25 2015 Colombia Bogotá, D.C. any adult 11223 2016 Colombia Bogotá, D.C. any adult 12686 2016 Colombia Guainía any adult 34 2015 Colombia Vichada any adult 48 2016 Colombia Cundinamarca any adult 4301 2015 Colombia Vichada any child 6 2015 Colombia Caquetá any adult 236 2016 Colombia Quindío any child 104 2016 Colombia Bolívar any child 118 2016 Colombia Santander any child 312 2015 Colombia Amazonas any adult 165 2016 Colombia Risaralda any adult 950 2017 Colombia La Guajira any adult 549 2017 Colombia Caquetá any adult 320 2015 Colombia Quindío any adult 733 2016 Colombia Valle del Cauca any child 338 2015 Colombia Córdoba any adult 490 2015 Colombia Tolima any adult 1195 2016 Colombia Tolima any child 167 2020 Colombia Santander any adult 1560 2017 Colombia Cundinamarca any child 557 2015 Colombia Córdoba any child 43 2016 Colombia Bolívar any adult 1600 2016 Colombia Guainía any child 7 2016 Colombia Nariño any child 96 2016 Colombia Amazonas any child 20 2017 Colombia Magdalena any child 135 2016 Colombia Arauca any adult 556 2015 Colombia Magdalena any child 133 2017 Colombia Amazonas any adult 118 2016 Colombia Guaviare any child 33 2015 Colombia Guainía any adult 48 2017 Colombia Boyacá any adult 1785 2016 Colombia Córdoba any child 54 2016 Colombia Sucre any adult 778 2017 Colombia La Guajira any child 57 2015 Colombia Risaralda any adult 982 2016 Colombia Cauca any adult 1056 2015 Colombia La Guajira any child 71 2015 Colombia Archipiélago de San Andrés, Providencia y Santa Catalina any child 23 2015 Colombia Putumayo any child 41 2017 Colombia Casanare any adult 979 2016 Colombia Cauca any child 103 2016 Colombia La Guajira any child 71 2015 Colombia Chocó any adult 275 2015 Colombia Guainía any child 7 2017 Colombia Magdalena any adult 1436 2016 Colombia Boyacá any child 241 2015 Colombia Santander any child 287 2016 Colombia Cesar any adult 1081 2017 Colombia Cesar any child 96 2016 Colombia Guaviare any adult 58 2017 Colombia Amazonas any child 19 2017 Colombia Antioquia any child 811 2015 Colombia Cauca any child 135 2015 Colombia La Guajira any adult 584 2016 Colombia Casanare any child 141 2017 Colombia Arauca any adult 510 2017 Colombia Archipiélago de San Andrés, Providencia y Santa Catalina any child 10 2015 Colombia Caldas any adult 779 2016 Colombia Vichada any child 4 2017 Colombia Caquetá any child 38 2015 Colombia Sucre any adult 703 2016 Colombia Santander any adult 2655 2017 Colombia Santander any adult 2478 2015 Colombia Atlántico any child 231 2019 Colombia Cauca any adult 1203 2015 Colombia Atlántico any adult 2540 2017 Colombia Quindío any adult 627 2017 Colombia Córdoba any adult 485 2017 Colombia Cauca any child 92 2016 Colombia Nariño any adult 1096 2017 Colombia Risaralda any adult 922 2017 Colombia Nariño a

In [0]:
colombian_df_aggregated = colombian_df_any.union(colombian_df_perpetrator)
colombian_df_aggregated.display()

year country department perpetrator age_group total_cases 2017 Colombia Cundinamarca any adult 3933 2022 Colombia Caldas any adult 481 2015 Colombia Casanare any adult 746 2017 Colombia Cesar any adult 1138 2016 Colombia Tolima any adult 1499 2015 Colombia Huila any child 217 2015 Colombia Tolima any child 153 2017 Colombia Quindío any child 98 2015 Colombia Nariño any child 107 2016 Colombia Boyacá any adult 1896 2017 Colombia Chocó any adult 209 2016 Colombia Norte de Santander any adult 1511 2017 Colombia Guainía any adult 27 2015 Colombia Casanare any child 152 2017 Colombia Guainía any child 6 2016 Colombia Valle del Cauca any adult 3721 2016 Colombia Cundinamarca any child 600 2015 Colombia Meta any child 259 2016 Colombia Huila any child 167 2015 Colombia Antioquia any adult 5476 2016 Colombia La Guajira any adult 554 2017 Colombia Huila any adult 1599 2017 Colombia Meta any adult 1873 2017 Colombia Putumayo any adult 268 2017 Colombia Atlántico any child 233 2017 Colombia Guaviare any adult 46 2015 Colombia Caquetá any child 16 2017 Colombia Valle del Cauca any child 345 2015 Colombia Norte de Santander any adult 1675 2017 Colombia Sucre any adult 753 2015 Colombia Chocó any child 25 2015 Colombia Bogotá, D.C. any adult 11223 2016 Colombia Bogotá, D.C. any adult 12686 2016 Colombia Guainía any adult 34 2015 Colombia Vichada any adult 48 2016 Colombia Cundinamarca any adult 4301 2015 Colombia Vichada any child 6 2015 Colombia Caquetá any adult 236 2016 Colombia Quindío any child 104 2016 Colombia Bolívar any child 118 2016 Colombia Santander any child 312 2015 Colombia Amazonas any adult 165 2016 Colombia Risaralda any adult 950 2017 Colombia La Guajira any adult 549 2017 Colombia Caquetá any adult 320 2015 Colombia Quindío any adult 733 2016 Colombia Valle del Cauca any child 338 2015 Colombia Córdoba any adult 490 2015 Colombia Tolima any adult 1195 2016 Colombia Tolima any child 167 2020 Colombia Santander any adult 1560 2017 Colombia Cundinamarca any child 557 2015 Colombia Córdoba any child 43 2016 Colombia Bolívar any adult 1600 2016 Colombia Guainía any child 7 2016 Colombia Nariño any child 96 2016 Colombia Amazonas any child 20 2017 Colombia Magdalena any child 135 2016 Colombia Arauca any adult 556 2015 Colombia Magdalena any child 133 2017 Colombia Amazonas any adult 118 2016 Colombia Guaviare any child 33 2015 Colombia Guainía any adult 48 2017 Colombia Boyacá any adult 1785 2016 Colombia Córdoba any child 54 2016 Colombia Sucre any adult 778 2017 Colombia La Guajira any child 57 2015 Colombia Risaralda any adult 982 2016 Colombia Cauca any adult 1056 2015 Colombia La Guajira any child 71 2015 Colombia Archipiélago de San Andrés, Providencia y Santa Catalina any child 23 2015 Colombia Putumayo any child 41 2017 Colombia Casanare any adult 979 2016 Colombia Cauca any child 103 2016 Colombia La Guajira any child 71 2015 Colombia Chocó any adult 275 2015 Colombia Guainía any child 7 2017 Colombia Magdalena any adult 1436 2016 Colombia Boyacá any child 241 2015 Colombia Santander any child 287 2016 Colombia Cesar any adult 1081 2017 Colombia Cesar any child 96 2016 Colombia Guaviare any adult 58 2017 Colombia Amazonas any child 19 2017 Colombia Antioquia any child 811 2015 Colombia Cauca any child 135 2015 Colombia La Guajira any adult 584 2016 Colombia Casanare any child 141 2017 Colombia Arauca any adult 510 2017 Colombia Archipiélago de San Andrés, Providencia y Santa Catalina any child 10 2015 Colombia Caldas any adult 779 2016 Colombia Vichada any child 4 2017 Colombia Caquetá any child 38 2015 Colombia Sucre any adult 703 2016 Colombia Santander any adult 2655 2017 Colombia Santander any adult 2478 2015 Colombia Atlántico any child 231 2019 Colombia Cauca any adult 1203 2015 Colombia Atlántico any adult 2540 2017 Colombia Quindío any adult 627 2017 Colombia Córdoba any adult 485 2017 Colombia Cauca any child 92 2016 Colombia Nariño any adult 1096 2017 Colombia Risaralda any adult 922 2017 Colombia Nariño a

In [0]:
colombian_df_all = colombian_df_aggregated.groupBy('year', 'country', 'perpetrator', 'age_group').agg(
    F.sum('total_cases').alias('total_cases')
).withColumn(
    'department', F.lit('all')
).select(
    F.col('year'),
    F.col('country'),
    F.col('department'),
    F.col('perpetrator'),
    F.col('age_group'),
    F.col('total_cases')
)
colombian_df_aggregated = colombian_df_aggregated.union(colombian_df_all)
colombian_df_all = colombian_df_aggregated.groupBy('year', 'country' ,'department', 'perpetrator').agg(
    F.sum('total_cases').alias('total_cases')
).withColumn(
    'age_group', F.lit('any')
).select(
    F.col('year'),
    F.col('country'),
    F.col('department'),
    F.col('perpetrator'),
    F.col('age_group'),
    F.col('total_cases')
)
colombian_df_aggregated.union(colombian_df_all).display()

year country department perpetrator age_group total_cases 2017 Colombia Cundinamarca any adult 3933 2022 Colombia Caldas any adult 481 2015 Colombia Casanare any adult 746 2017 Colombia Cesar any adult 1138 2016 Colombia Tolima any adult 1499 2015 Colombia Huila any child 217 2015 Colombia Tolima any child 153 2017 Colombia Quindío any child 98 2015 Colombia Nariño any child 107 2016 Colombia Boyacá any adult 1896 2017 Colombia Chocó any adult 209 2016 Colombia Norte de Santander any adult 1511 2017 Colombia Guainía any adult 27 2015 Colombia Casanare any child 152 2017 Colombia Guainía any child 6 2016 Colombia Valle del Cauca any adult 3721 2016 Colombia Cundinamarca any child 600 2015 Colombia Meta any child 259 2016 Colombia Huila any child 167 2015 Colombia Antioquia any adult 5476 2016 Colombia La Guajira any adult 554 2017 Colombia Huila any adult 1599 2017 Colombia Meta any adult 1873 2017 Colombia Putumayo any adult 268 2017 Colombia Atlántico any child 233 2017 Colombia Guaviare any adult 46 2015 Colombia Caquetá any child 16 2017 Colombia Valle del Cauca any child 345 2015 Colombia Norte de Santander any adult 1675 2017 Colombia Sucre any adult 753 2015 Colombia Chocó any child 25 2015 Colombia Bogotá, D.C. any adult 11223 2016 Colombia Bogotá, D.C. any adult 12686 2016 Colombia Guainía any adult 34 2015 Colombia Vichada any adult 48 2016 Colombia Cundinamarca any adult 4301 2015 Colombia Vichada any child 6 2015 Colombia Caquetá any adult 236 2016 Colombia Quindío any child 104 2016 Colombia Bolívar any child 118 2016 Colombia Santander any child 312 2015 Colombia Amazonas any adult 165 2016 Colombia Risaralda any adult 950 2017 Colombia La Guajira any adult 549 2017 Colombia Caquetá any adult 320 2015 Colombia Quindío any adult 733 2016 Colombia Valle del Cauca any child 338 2015 Colombia Córdoba any adult 490 2015 Colombia Tolima any adult 1195 2016 Colombia Tolima any child 167 2020 Colombia Santander any adult 1560 2017 Colombia Cundinamarca any child 557 2015 Colombia Córdoba any child 43 2016 Colombia Bolívar any adult 1600 2016 Colombia Guainía any child 7 2016 Colombia Nariño any child 96 2016 Colombia Amazonas any child 20 2017 Colombia Magdalena any child 135 2016 Colombia Arauca any adult 556 2015 Colombia Magdalena any child 133 2017 Colombia Amazonas any adult 118 2016 Colombia Guaviare any child 33 2015 Colombia Guainía any adult 48 2017 Colombia Boyacá any adult 1785 2016 Colombia Córdoba any child 54 2016 Colombia Sucre any adult 778 2017 Colombia La Guajira any child 57 2015 Colombia Risaralda any adult 982 2016 Colombia Cauca any adult 1056 2015 Colombia La Guajira any child 71 2015 Colombia Archipiélago de San Andrés, Providencia y Santa Catalina any child 23 2015 Colombia Putumayo any child 41 2017 Colombia Casanare any adult 979 2016 Colombia Cauca any child 103 2016 Colombia La Guajira any child 71 2015 Colombia Chocó any adult 275 2015 Colombia Guainía any child 7 2017 Colombia Magdalena any adult 1436 2016 Colombia Boyacá any child 241 2015 Colombia Santander any child 287 2016 Colombia Cesar any adult 1081 2017 Colombia Cesar any child 96 2016 Colombia Guaviare any adult 58 2017 Colombia Amazonas any child 19 2017 Colombia Antioquia any child 811 2015 Colombia Cauca any child 135 2015 Colombia La Guajira any adult 584 2016 Colombia Casanare any child 141 2017 Colombia Arauca any adult 510 2017 Colombia Archipiélago de San Andrés, Providencia y Santa Catalina any child 10 2015 Colombia Caldas any adult 779 2016 Colombia Vichada any child 4 2017 Colombia Caquetá any child 38 2015 Colombia Sucre any adult 703 2016 Colombia Santander any adult 2655 2017 Colombia Santander any adult 2478 2015 Colombia Atlántico any child 231 2019 Colombia Cauca any adult 1203 2015 Colombia Atlántico any adult 2540 2017 Colombia Quindío any adult 627 2017 Colombia Córdoba any adult 485 2017 Colombia Cauca any child 92 2016 Colombia Nariño any adult 1096 2017 Colombia Risaralda any adult 922 2017 Colombia Nariño a